In [3]:
pip install rasterio

Note: you may need to restart the kernel to use updated packages.


In [4]:
pip install xarray-spatial

  Obtaining dependency information for xarray-spatial from https://files.pythonhosted.org/packages/d2/15/b89704ba16140a9fce8973b6612d96cf962188b7830959b314ed3b5d6db7/xarray_spatial-0.3.7-py3-none-any.whl.metadata
  Using cached xarray_spatial-0.3.7-py3-none-any.whl.metadata (15 kB)
  Obtaining dependency information for datashader from https://files.pythonhosted.org/packages/a3/b7/d6e22439282f92009fd74efa73287af02355d3d5c00f771be40ef9b1688a/datashader-0.16.0-py2.py3-none-any.whl.metadata
  Using cached datashader-0.16.0-py2.py3-none-any.whl.metadata (11 kB)
     ---------------------------------------- 0.0/14.7 MB ? eta -:--:--
     ---------------------------------------- 0.0/14.7 MB ? eta -:--:--
     --------------------------------------- 0.1/14.7 MB 653.6 kB/s eta 0:00:23
     - -------------------------------------- 0.4/14.7 MB 2.5 MB/s eta 0:00:06
     -- ------------------------------------- 0.7/14.7 MB 3.9 MB/s eta 0:00:04
     -- ------------------------------------- 1.0/14.7

ERROR: Could not install packages due to an OSError: [WinError 5] Access is denied: 'C:\\Anaconda3\\envs\\suzan\\Lib\\site-packages\\~umpy.libs\\libopenblas64__v0.3.23-293-gc2f4bdbb-gcc_10_3_0-2bde3a66a51006b2b53eb373ff767a3f.dll'
Consider using the `--user` option or check the permissions.



In [14]:
pip install geemap

Note: you may need to restart the kernel to use updated packages.


In [1]:
import rasterio
import geopandas as gpd
import ee
import numpy as np
from rasterio import windows, warp, features
from rasterio.mask import geometry_mask
from PIL import Image
import xarray as xr
import geemap

# Authenticate to Earth Engine
ee.Authenticate()
ee.Initialize()

Enter verification code:  4/1AfJohXnOP0NlXN2km9jY01SX8Ahqw_7k7ujV3mQdUHkCAal0J9r6UlF79T4



Successfully saved authorization token.


# Data collection

In [8]:
# Initialize the Earth Engine module.
ee.Initialize()

# Specify the season of interest
start_date = '2022-06-01'
end_date = '2022-09-30'
time_of_interest = ee.DateRange(ee.Date(start_date), ee.Date(end_date))

# Read your GeoDataFrame from a shapefile
gdf = gpd.read_file(r'F:\Suzan\Quality_Assessment\New_folder_DS\Downscaling\Data\Shapefiles\Study_area_Mwea.shp')

# Function to format a Shapely geometry to a GeoJSON-like dictionary
def format_geometry(geometry):
    if geometry.geom_type == 'Polygon':
        coordinates = [list(coord) for coord in geometry.exterior.coords]
        return {
            "type": "Polygon",
            "coordinates": [coordinates]
        }
    else:
        return None

# Apply the formatting function to the 'geometry' column
gdf['formatted_geometry'] = gdf['geometry'].apply(format_geometry)

# Convert the column to a list of dictionaries
formatted_geometry_list = gdf['formatted_geometry'].tolist()

# Assuming the first geometry in the list is the area of interest
area_of_interest = ee.Geometry(formatted_geometry_list[0])

# Use the Earth Engine Python API to search for Sentinel-2 images
collection = (ee.ImageCollection("COPERNICUS/S2_SR_HARMONIZED)
              .filterBounds(area_of_interest)
              .filterDate(time_of_interest)
              .filterMetadata('CLOUDY_PIXEL_PERCENTAGE', 'less_than', 95))

# Get a list of image IDs
image_ids = collection.aggregate_array('system:id').getInfo()

print(f'{len(image_ids)} products were collected.')

# Function to create a true color image
def create_true_color_image(image):
    return image.select(['B4', 'B3', 'B2'])  # Red, Green, Blue

# Lists to store NDVI data and true color images
ndvi_sub = []
true_color_imgs = []

# Loop through each image
for image_id in image_ids:
    # Load the image
    image = ee.Image(image_id)

    # Clip the image to the area of interest
    clipped_image = image.clip(area_of_interest)

    # Calculate NDVI
    ndvi_image = clipped_image.normalizedDifference(['B8', 'B4']).rename('NDVI')
    
    # Reduce the region to compute statistics
    stats = ndvi_image.reduceRegion(
        reducer=ee.Reducer.mean(),
        geometry=area_of_interest,
        scale=10  # Adjust the scale as needed
    )

    # Get the mean NDVI value
    ndvi_value = stats.get('NDVI')
    ndvi_sub.append(ndvi_value.getInfo())

    # Create true color image
    true_color_image = create_true_color_image(clipped_image)
    true_color_imgs.append(true_color_image)

    # Export NDVI image to Google Drive
    ndvi_filename = f'NDVI_{image_id.split("/")[-1]}'
    ndvi_task = ee.batch.Export.image.toDrive(
        image=ndvi_image,
        region=area_of_interest.bounds().getInfo()['coordinates'],
        description=ndvi_filename,
        folder="NDVI_out",
        fileFormat="GeoTIFF"
    )
    ndvi_task.start()

    # Export True Color image to Google Drive
    true_color_filename = f'TrueColor_{image_id.split("/")[-1]}'
    true_color_task = ee.batch.Export.image.toDrive(
        image=true_color_image,
        region=area_of_interest.bounds().getInfo()['coordinates'],
        description=true_color_filename,
        folder="TrueColor_out",
        fileFormat="GeoTIFF"
    )
    true_color_task.start()

    print(f"Exporting NDVI {ndvi_filename} and True Color {true_color_filename}...")



43 products were collected.
Exporting NDVI NDVI_20220602T073621_20220602T075846_T37MBV and True Color TrueColor_20220602T073621_20220602T075846_T37MBV...
Exporting NDVI NDVI_20220602T073621_20220602T075846_T37MCV and True Color TrueColor_20220602T073621_20220602T075846_T37MCV...
Exporting NDVI NDVI_20220607T073619_20220607T075441_T37MBV and True Color TrueColor_20220607T073619_20220607T075441_T37MBV...
Exporting NDVI NDVI_20220607T073619_20220607T075441_T37MCV and True Color TrueColor_20220607T073619_20220607T075441_T37MCV...
Exporting NDVI NDVI_20220612T073621_20220612T075450_T37MBV and True Color TrueColor_20220612T073621_20220612T075450_T37MBV...
Exporting NDVI NDVI_20220612T073621_20220612T075450_T37MCV and True Color TrueColor_20220612T073621_20220612T075450_T37MCV...
Exporting NDVI NDVI_20220617T073619_20220617T075444_T37MBV and True Color TrueColor_20220617T073619_20220617T075444_T37MBV...
Exporting NDVI NDVI_20220617T073619_20220617T075444_T37MCV and True Color TrueColor_202206